In [1]:
%load_ext jupyter_black

In [2]:
import spotipy
from spotipy.oauth2 import SpotifyOAuth
import os
import sys
import pandas as pd
import numpy as np
import requests
from spotify_dl import spotify_dl
from pathlib import Path
import time
import os
from dotenv import load_dotenv  # changed magic command to explicit load
import librosa
import matplotlib.pyplot as plt
from datetime import datetime
from sklearn.metrics import pairwise
from sklearn.model_selection import train_test_split
from typing import List
from flask import Flask, redirect, request
import random
import tensorflow as tf
from tensorflow.keras.models import Sequential, Model
from tensorflow.keras.layers import Conv2D  # new
from tensorflow.keras.layers import MaxPooling2D  # new
from tensorflow.keras.layers import Flatten  # new
from tensorflow.keras.layers import Dense
from tensorflow.keras.layers import Dropout
from tensorflow.keras.applications import ResNet50V2
from tensorflow.keras.callbacks import EarlyStopping
from skimage.transform import resize


pd.set_option("display.max_rows", None)  # pandas dataframe formatting options
pd.set_option("display.max_columns", None)
# pd.options.display.float_format = "{:,.2f}".format


custom_env_path = "../../brainstation_capstone_cfg.env"  # environment variables file

## Feature Function Definitions

In [3]:
# How was this solved? sampling rate must be explicitly passed to every function
# This includes the display function itself!
# Hence, the sampling rate is now an output from the function itself
def get_mfcc(y, sr):
    mfcc = librosa.power_to_db(librosa.feature.mfcc(y=y, sr=sr), ref=np.max)
    return mfcc


def get_melspectrogram(y, sr):
    melspectrogram = librosa.power_to_db(
        librosa.feature.melspectrogram(y=y, sr=sr), ref=np.max
    )
    # this is a power spectrum (amplitude squared)
    return melspectrogram


def get_chroma_vector(y, sr):
    chroma = librosa.feature.chroma_stft(y=y, sr=sr)
    return chroma


def get_tonnetz(y, sr):
    tonnetz = librosa.feature.tonnetz(y=y, sr=sr)
    return tonnetz


def get_feature(input_file_path, track_id):
    # Load data
    y, sr = librosa.load(
        input_file_path,
        sr=None,
        offset=10,
        duration=120,
    )
    # Extracting MFCC feature
    mfcc = get_mfcc(y, sr)
    # Move save step to this point!
    np.save(f"../data/vectorized_mp3s/raw/mfcc_{track_id}.npy", mfcc)
    mfcc_mean = mfcc.mean(axis=1)
    mfcc_min = mfcc.min(axis=1)
    mfcc_max = mfcc.max(axis=1)
    mfcc_feature = np.concatenate((mfcc_mean, mfcc_min, mfcc_max))

    # Need to move the save to before the reduction of features

    # Extracting Mel Spectrogram feature
    melspectrogram = get_melspectrogram(y, sr)
    np.save(
        f"../data/vectorized_mp3s/raw/melspectrogram_{track_id}.npy",
        melspectrogram,
    )
    melspectrogram_mean = melspectrogram.mean(axis=1)
    melspectrogram_min = melspectrogram.min(axis=1)
    melspectrogram_max = melspectrogram.max(axis=1)
    melspectrogram_feature = np.concatenate(
        (melspectrogram_mean, melspectrogram_min, melspectrogram_max)
    )

    # Extracting chroma vector feature
    chroma = get_chroma_vector(y, sr)
    np.save(f"../data/vectorized_mp3s/raw/chroma_{track_id}.npy", chroma)
    chroma_mean = chroma.mean(axis=1)
    chroma_min = chroma.min(axis=1)
    chroma_max = chroma.max(axis=1)
    chroma_feature = np.concatenate((chroma_mean, chroma_min, chroma_max))

    # Extracting tonnetz feature
    tntz = get_tonnetz(y, sr)
    np.save(f"../data/vectorized_mp3s/raw/tonnetz_{track_id}.npy", tntz)
    tntz_mean = tntz.mean(axis=1)
    tntz_min = tntz.min(axis=1)
    tntz_max = tntz.max(axis=1)
    tntz_feature = np.concatenate((tntz_mean, tntz_min, tntz_max))

    # return chroma_feature, melspectrogram_feature, mfcc_feature, tntz_feature
    # this returns both the pairwise vector feature and the CNN feature
    pairwise_feature = np.concatenate(
        (chroma_feature, melspectrogram_feature, mfcc_feature, tntz_feature)
    )
    height = 224
    width = 224
    mel_resize = resize(melspectrogram, (height, width))
    chroma_resize = resize(chroma, (height, width))
    tntz_resize = resize(tntz, (height, width))
    layers = [mel_resize, chroma_resize, tntz_resize]
    image_stack = []
    for layer in layers:
        max_val = layer.max()
        min_val = layer.min()
        range = max_val - min_val
        range = max(range, 1.0)
        # need to have this to handle division by 0
        norm = (layer - min_val) / range
        image_stack.append(norm.astype(np.float32))
    cnn_feature = np.dstack(image_stack)
    return pairwise_feature, cnn_feature

## CNN Model Setup

In [4]:
def set_random_seed(seed):
    """Random seeds for reproducability"""

    random.seed(seed)
    tf.random.set_seed(seed)

In [5]:
height = 224
width = 224
channels = 3
res_model = ResNet50V2(
    weights="imagenet", include_top=True, input_shape=(height, width, channels)
)
res_model.summary()

Model: "resnet50v2"
__________________________________________________________________________________________________
 Layer (type)                Output Shape                 Param #   Connected to                  
 input_1 (InputLayer)        [(None, 224, 224, 3)]        0         []                            
                                                                                                  
 conv1_pad (ZeroPadding2D)   (None, 230, 230, 3)          0         ['input_1[0][0]']             
                                                                                                  
 conv1_conv (Conv2D)         (None, 112, 112, 64)         9472      ['conv1_pad[0][0]']           
                                                                                                  
 pool1_pad (ZeroPadding2D)   (None, 114, 114, 64)         0         ['conv1_conv[0][0]']          
                                                                                         

In [6]:
# Freeze all the layers in the base model
for layer in res_model.layers:
    layer.trainable = False

In [7]:
# For image analysis we only need to flatten for embedding
set_random_seed(121)
res_out = res_model.output
output = Flatten()(res_out)

In [8]:
model = Model(inputs=res_model.input, outputs=output)
model.summary()

Model: "model"
__________________________________________________________________________________________________
 Layer (type)                Output Shape                 Param #   Connected to                  
 input_1 (InputLayer)        [(None, 224, 224, 3)]        0         []                            
                                                                                                  
 conv1_pad (ZeroPadding2D)   (None, 230, 230, 3)          0         ['input_1[0][0]']             
                                                                                                  
 conv1_conv (Conv2D)         (None, 112, 112, 64)         9472      ['conv1_pad[0][0]']           
                                                                                                  
 pool1_pad (ZeroPadding2D)   (None, 114, 114, 64)         0         ['conv1_conv[0][0]']          
                                                                                              

## Vectorize Data

### Count MP3s

In [9]:
data_dir = Path("../data/mp3s/")
path_glob = data_dir.rglob("*.mp3")
pairwise_file_paths = []
for pairwise_file_path in path_glob:
    pairwise_file_paths.append(
        pairwise_file_path
    )  # creates a list for repeated iteration
    # if this is not done, the .rglob command above has to be repeated to regenerate iterator
len(pairwise_file_paths)  # number of mp3s in directory

11578

### Generate Track Feature Files

#### Pairwise Parquet and CNN Matrices

In [16]:
# Generator objects need to be rerun each time to prevent exhaustion
data_dir = Path("../data/mp3s/")
output_pairwise_dir = Path("../data/vectorized_mp3s/pairwise_parquets/")
output_cnn_dir = Path("../data/vectorized_mp3s/cnn_parquets/")
data_dir_glob = data_dir.rglob("*.mp3")
output_pairwise_glob = output_pairwise_dir.rglob("*.parquet")
output_cnn_glob = output_cnn_dir.rglob("*.parquet")
count = 1
file_paths = [file_path for file_path in data_dir_glob]
print("Number of MP3 Files: ", len(file_paths), "\n")
pairwise_track_ids = [file_path.stem for file_path in output_pairwise_glob]
cnn_track_ids = [file_path.stem for file_path in output_cnn_glob]
for file_path in file_paths:
    print(f"{count}. MP3 FILE PATH: \n", f"{file_path}")
    path_split = str(file_path).split("/")
    track_id = path_split[3]
    pairwise_track, cnn_track = get_feature(file_path, track_id)
    if (len(pairwise_track_ids) > 0) & (track_id in pairwise_track_ids):
        print(f"{track_id} has already been vectorized for pairwise...skipping...")
    else:
        vectorized_df = pd.DataFrame(pairwise_track).T
        vectorized_df["track_id"] = track_id
        vectorized_df = vectorized_df.set_index(vectorized_df.track_id).drop(
            columns="track_id"
        )
        vectorized_df.columns = vectorized_df.columns.astype(str)
        vectorized_df.to_parquet(
            f"../data/vectorized_mp3s/pairwise_parquets/{track_id}.parquet"
        )
        print(f"{track_id} has been pairwise vectorized!")
    if (len(cnn_track_ids) > 0) & (track_id in cnn_track_ids):
        print(f"{track_id} has already been vectorized for CNN...skipping...\n")
        count += 1
    else:
        cnn_track = np.expand_dims(cnn_track, axis=0)
        cnn_track = model.predict(cnn_track)
        vectorized_df = pd.DataFrame(cnn_track)
        vectorized_df["track_id"] = track_id
        vectorized_df = vectorized_df.set_index(vectorized_df.track_id).drop(
            columns="track_id"
        )
        vectorized_df.columns = vectorized_df.columns.astype(str)
        vectorized_df.to_parquet(
            f"../data/vectorized_mp3s/cnn_parquets/{track_id}.parquet"
        )
        print(f"{track_id} has been CNN vectorized!\n")
        count += 1

Number of MP3 Files:  11578 

1. MP3 FILE PATH: 
 ../data/mp3s/1ZB2qWsheGabSEYvBYxjKn/Take on Me/Weezer - Take on Me.mp3
1ZB2qWsheGabSEYvBYxjKn has already been vectorized for pairwise...skipping...
1ZB2qWsheGabSEYvBYxjKn has already been vectorized for CNN...skipping...

2. MP3 FILE PATH: 
 ../data/mp3s/5V9H9J5GcUGY5ig029g5OU/Shkleepy/Manwolves - Shkleepy.mp3
5V9H9J5GcUGY5ig029g5OU has already been vectorized for pairwise...skipping...
5V9H9J5GcUGY5ig029g5OU has already been vectorized for CNN...skipping...

3. MP3 FILE PATH: 
 ../data/mp3s/34FsCOAQ0U99vAh3uoiLmm/Bandana (feat. Young Buck)/Dirty Audio, BL3R, Young Buck - Bandana (feat. Young Buck).mp3
34FsCOAQ0U99vAh3uoiLmm has already been vectorized for pairwise...skipping...
34FsCOAQ0U99vAh3uoiLmm has already been vectorized for CNN...skipping...

4. MP3 FILE PATH: 
 ../data/mp3s/25mldAmMHYzXhDXCxTpTHy/Chloroform/Phoenix - Chloroform.mp3
25mldAmMHYzXhDXCxTpTHy has already been vectorized for pairwise...skipping...
25mldAmMHYzXhDXCx

63ElaCh1e2AosE7EJAdxfq has already been vectorized for pairwise...skipping...
1/1 [==============================] - 0s 115ms/step
63ElaCh1e2AosE7EJAdxfq has been CNN vectorized!

858. MP3 FILE PATH: 
 ../data/mp3s/7BDGjDqOuUbZkwDPSXoMl0/Saturday Night/The Cat Empire - Saturday Night.mp3
7BDGjDqOuUbZkwDPSXoMl0 has already been vectorized for pairwise...skipping...
1/1 [==============================] - 0s 147ms/step
7BDGjDqOuUbZkwDPSXoMl0 has been CNN vectorized!

859. MP3 FILE PATH: 
 ../data/mp3s/6R40BJoXMj9R942vnhuFsS/Kenner Boogie/Jon Batiste - Kenner Boogie.mp3
6R40BJoXMj9R942vnhuFsS has already been vectorized for pairwise...skipping...
1/1 [==============================] - 0s 124ms/step
6R40BJoXMj9R942vnhuFsS has been CNN vectorized!

860. MP3 FILE PATH: 
 ../data/mp3s/0FeqPtdkwXs54spLxfWnqr/Smoke Ring Halo/The Wood Brothers - Smoke Ring Halo.mp3
0FeqPtdkwXs54spLxfWnqr has already been vectorized for pairwise...skipping...
1/1 [==============================] - 0s 120ms/step
0F

/Users/vii/anaconda3/envs/brainstation_capstone/lib/python3.8/site-packages/librosa/core/pitch.py:102: UserWarning: Trying to estimate tuning from empty frequency set.
  return pitch_tuning(


7wobmC9Xz4stYN1ZVLWgi5 has already been vectorized for pairwise...skipping...
1/1 [==============================] - 0s 128ms/step
7wobmC9Xz4stYN1ZVLWgi5 has been CNN vectorized!

1394. MP3 FILE PATH: 
 ../data/mp3s/3mskluxUoD4xICumdJCR7l/Dave McGillivray/Jeff Beal - Dave McGillivray.mp3
3mskluxUoD4xICumdJCR7l has already been vectorized for pairwise...skipping...
1/1 [==============================] - 0s 161ms/step
3mskluxUoD4xICumdJCR7l has been CNN vectorized!

1395. MP3 FILE PATH: 
 ../data/mp3s/0XVQTr58DZbLUcjacnTp8k/Madness/Ruelle - Madness.mp3
0XVQTr58DZbLUcjacnTp8k has already been vectorized for pairwise...skipping...
1/1 [==============================] - 0s 125ms/step
0XVQTr58DZbLUcjacnTp8k has been CNN vectorized!

1396. MP3 FILE PATH: 
 ../data/mp3s/18765csbulflFn1Ww4bcys/Change/Clay Walker - Change.mp3
18765csbulflFn1Ww4bcys has already been vectorized for pairwise...skipping...
1/1 [==============================] - 0s 148ms/step
18765csbulflFn1Ww4bcys has been CNN vecto

/Users/vii/anaconda3/envs/brainstation_capstone/lib/python3.8/site-packages/librosa/core/pitch.py:102: UserWarning: Trying to estimate tuning from empty frequency set.
  return pitch_tuning(


...

6cZ8T2c95NfRTrGEXqThIq has already been vectorized for pairwise...skipping...
1/1 [==============================] - 0s 150ms/step
6cZ8T2c95NfRTrGEXqThIq has been CNN vectorized!

10165. MP3 FILE PATH: 
 ../data/mp3s/2a7z0RvsjwSMWEPwIWO5z2/La Ultima Vez/Feid - La Ultima Vez.mp3
2a7z0RvsjwSMWEPwIWO5z2 has already been vectorized for pairwise...skipping...
1/1 [==============================] - 0s 137ms/step
2a7z0RvsjwSMWEPwIWO5z2 has been CNN vectorized!

10166. MP3 FILE PATH: 
 ../data/mp3s/7os1J5P6JqIxKSxq71QuQC/Hero (feat. Christina Perri) - Deep Mix/Cash Cash, Christina Perri - Hero (feat. Christina Perri) - Deep Mix.mp3
7os1J5P6JqIxKSxq71QuQC has already been vectorized for pairwise...skipping...
1/1 [==============================] - 0s 139ms/step
7os1J5P6JqIxKSxq71QuQC has been CNN vectorized!

10167. MP3 FILE PATH: 
 ../data/mp3s/4qZwVr553XcQNdeqjueeE3/Roses Are Red - Original Version/Aqua - Roses Are Red - Original Version.mp3
4qZwVr553XcQNdeqjueeE3 has already been vectorized 

/Users/vii/anaconda3/envs/brainstation_capstone/lib/python3.8/site-packages/librosa/core/pitch.py:102: UserWarning: Trying to estimate tuning from empty frequency set.
  return pitch_tuning(


2s9M78CDrQDjB2D827XXr4 has already been vectorized for pairwise...skipping...
1/1 [==============================] - 0s 129ms/step
2s9M78CDrQDjB2D827XXr4 has been CNN vectorized!

10205. MP3 FILE PATH: 
 ../data/mp3s/3rMyMv8EjKXoPnaRo2hdJN/Stuntin' Like My Daddy - Street/Birdman, Lil Wayne - Stuntin' Like My Daddy - Street.mp3
3rMyMv8EjKXoPnaRo2hdJN has already been vectorized for pairwise...skipping...
1/1 [==============================] - 0s 124ms/step
3rMyMv8EjKXoPnaRo2hdJN has been CNN vectorized!

10206. MP3 FILE PATH: 
 ../data/mp3s/3UUx0JWEJCbKZvhzpruLfe/Letting You Go/Sara Evans - Letting You Go.mp3
3UUx0JWEJCbKZvhzpruLfe has already been vectorized for pairwise...skipping...
1/1 [==============================] - 0s 136ms/step
3UUx0JWEJCbKZvhzpruLfe has been CNN vectorized!

10207. MP3 FILE PATH: 
 ../data/mp3s/3As1HTUDBTiTDbwnuICy4C/Fisherman's Horizon Piano Collections Version (From Final Fantasy VIII) [For Piano Solo]/Nobuo Uematsu, daigoro789 - #Fisherman's Horizon# Piano

/Users/vii/anaconda3/envs/brainstation_capstone/lib/python3.8/site-packages/librosa/core/spectrum.py:256: UserWarning: n_fft=1024 is too large for input signal of length=818
  warnings.warn(


4FwxXaVT6iGfhiInzQLJ2n has been CNN vectorized!

11450. MP3 FILE PATH: 
 ../data/mp3s/6QPCo7i6vBXzbdg4muyOdG/Bye Bye Blackbird/Riders In The Sky - Bye Bye Blackbird.mp3
6QPCo7i6vBXzbdg4muyOdG has already been vectorized for pairwise...skipping...
1/1 [==============================] - 0s 143ms/step
6QPCo7i6vBXzbdg4muyOdG has been CNN vectorized!

11451. MP3 FILE PATH: 
 ../data/mp3s/2v4kQsvlTPEYOIyJkytzGH/In A Sweater Poorly Knit/mewithoutYou - In A Sweater Poorly Knit.mp3
2v4kQsvlTPEYOIyJkytzGH has already been vectorized for pairwise...skipping...
1/1 [==============================] - 0s 134ms/step
2v4kQsvlTPEYOIyJkytzGH has been CNN vectorized!

11452. MP3 FILE PATH: 
 ../data/mp3s/1eupQ3yeBQPmAUcHyhrXkb/Mal ô mains/Sanseverino - Mal ô mains.mp3
1eupQ3yeBQPmAUcHyhrXkb has already been vectorized for pairwise...skipping...
1/1 [==============================] - 0s 122ms/step
1eupQ3yeBQPmAUcHyhrXkb has been CNN vectorized!

11453. MP3 FILE PATH: 
 ../data/mp3s/6FlgXdr8JJLfQvMoHQjE0r/

#### Create Complete Pairwise Parquet

In [17]:
vectorized_data_path = Path("../data/vectorized_mp3s/pairwise_parquets/")
path_glob = vectorized_data_path.rglob("*.parquet")
dataframes = []
for file_path in path_glob:
    tmp = pd.read_parquet(f"{file_path}")
    dataframes.append(tmp)
vectorized_df = pd.concat(dataframes)

In [18]:
output_file_date = datetime.now().strftime(
    "%Y%m%d"
)  # time stamps the file with the reverse of the date
vectorized_df.to_parquet(
    f"../data/vectorized_mp3s/pairwise_complete_parquets/{output_file_date}_complete_pairwise_data.parquet"
)
assert vectorized_df.shape[0] == 11578

#### Create Complete CNN Parquet

In [19]:
vectorized_data_path = Path("../data/vectorized_mp3s/cnn_parquets/")
path_glob = vectorized_data_path.rglob("*.parquet")
dataframes = []
for file_path in path_glob:
    tmp = pd.read_parquet(f"{file_path}")
    dataframes.append(tmp)
vectorized_df = pd.concat(dataframes)

In [20]:
output_file_date = datetime.now().strftime(
    "%Y%m%d"
)  # time stamps the file with the reverse of the date
vectorized_df.to_parquet(
    f"../data/vectorized_mp3s/cnn_complete_parquets/{output_file_date}_complete_cnn_data.parquet"
)
assert vectorized_df.shape[0] == 11578